### Machine Learning Project

## 21MAT 219 Soumen 

###### Dataset Description

The classification goal is to predict whether the patient has $10$ year risk of future heart diseases. 


* Sex : male or female

* Age : Age of the patient

* Current Smoker : Whether or not the patient is a current smoker.

* Cigs Per Day : the number of cigarettes that the person smoked on average in one day.

* Bp Meds : Whether or not the patient was on blood pressure medication.

* Prevalent Stroke : Whether or not the patient had previously had a stroke.

* Prevalent Hyp : whether or not the patient was hypertensive.

* Diabetes : whether or not the patient had diabetes.

* Tot Chol : total cholesterol level

* Sys BP : systolic blood pressure.

* Dia BP : diastolic blood pressure.

* BMI : Body mass index

* Heart rate : heart rate

* Glucose : glucose level

**Predict Variable :**

* $10$ year risk of heart disease(binary : "1" means "yes","0" means "no").

In [1]:
using CSV,DataFrames,Statistics,StatsBase;

In [2]:
using GLM,Lathe,MLBase

In [3]:
using StatsPlots;

In [4]:
using Plots # ,BoxCoxTrans;


In [5]:
data = DataFrame(CSV.File("framingham heart disease.csv"));

In [9]:
Lathe.preprocess.OneHotEncoder(data)

LoadError: MethodError: no method matching OneHotEncoder(::DataFrame)
[0mClosest candidates are:
[0m  OneHotEncoder() at C:\Users\hp\.julia\packages\Lathe\solhV\src\preprocess\encoding.jl:19

In [7]:
show(data,allcols = true)

4238×16 DataFrame
│ Row  │ male  │ age   │ education │ currentSmoker │ cigsPerDay │ BPMeds  │
│      │ Int64 │ Int64 │ String3   │ Int64         │ String3    │ String3 │
├──────┼───────┼───────┼───────────┼───────────────┼────────────┼─────────┤
│ 1    │ 1     │ 39    │ 4         │ 0             │ 0          │ 0       │
│ 2    │ 0     │ 46    │ 2         │ 0             │ 0          │ 0       │
│ 3    │ 1     │ 48    │ 1         │ 1             │ 20         │ 0       │
│ 4    │ 0     │ 61    │ 3         │ 1             │ 30         │ 0       │
│ 5    │ 0     │ 46    │ 3         │ 1             │ 23         │ 0       │
│ 6    │ 0     │ 43    │ 2         │ 0             │ 0          │ 0       │
│ 7    │ 0     │ 63    │ 1         │ 0             │ 0          │ 0       │
│ 8    │ 0     │ 45    │ 2         │ 1             │ 20         │ 0       │
│ 9    │ 1     │ 52    │ 1         │ 0             │ 0          │ 0       │
│ 10   │ 1     │ 43    │ 1         │ 1             │ 30         │ 0   

In [22]:
describe(data)

16×8 typename(DataFrame). Omitted printing of 2 columns
│ Row │ variable        │ mean       │ min   │ median │ max   │ nunique │
│     │ Symbol          │ Union…     │ Any   │ Union… │ Any   │ Union…  │
├─────┼─────────────────┼────────────┼───────┼────────┼───────┼─────────┤
│ 1   │ male            │ 0.429212   │ 0     │ 0.0    │ 1     │         │
│ 2   │ age             │ 49.5849    │ 32    │ 49.0   │ 70    │         │
│ 3   │ education       │            │ 1     │        │ NA    │ 5       │
│ 4   │ currentSmoker   │ 0.494101   │ 0     │ 0.0    │ 1     │         │
│ 5   │ cigsPerDay      │            │ 0     │        │ NA    │ 34      │
│ 6   │ BPMeds          │            │ 0     │        │ NA    │ 3       │
│ 7   │ prevalentStroke │ 0.00589901 │ 0     │ 0.0    │ 1     │         │
│ 8   │ prevalentHyp    │ 0.310524   │ 0     │ 0.0    │ 1     │         │
│ 9   │ diabetes        │ 0.0257197  │ 0     │ 0.0    │ 1     │         │
│ 10  │ totChol         │            │ 107   │        │ NA    │ 249     │
│ 11  │ sysBP           │ 132.352    │ 83.5  │ 128.0  │ 295.0 │         │
│ 12  │ diaBP           │ 82.8935    │ 48.0  │ 82.0   │ 142.5 │         │
│ 13  │ BMI             │            │ 15.54 │        │ NA    │ 1364    │
│ 14  │ heartRate       │            │ 100   │        │ NA    │ 74      │
│ 15  │ glucose         │            │ 100   │        │ NA    │ 144     │
│ 16  │ TenYearCHD      │ 0.151958   │ 0     │ 0.0    │ 1     │         │

##### Trating the missing values

In [23]:
s = data[:,[3,5,6,10,13,14,15]]; # these are the columns where we have NA values
# s is a dataframe

In [24]:
v = [s[!,i] for i in range(start = 1,stop =size(s)[2],step = 1)];
# converting the  dataframe column into vector

In [25]:
# replacing the na values by -10, this is just a choice to distinguish from the other values
for i in 1:7
    replace!(v[i],"NA" => "-10")
end

In [26]:
v = [parse.(Float64,v[k]) for k in 1:length(v)];

In [27]:
medians = [median(v[i]) for i in 1:7];
# calculation of medians for all the columns which has NA values

In [28]:
medians

7-element Vector{Float64}:
   2.0
   0.0
   0.0
 233.0
  25.38
  75.0
  77.0

In [29]:
# replacing the na values by medians in respective column
v = [replace!(v[i],-10 => medians[i]) for i in 1:7];

In [30]:
data = select(data, Not([3,5,6,10,13,14,15]));
# removing the columns which has na values from original dataset

In [31]:
# inserting the changed column in their respective postion
data = insertcols!(data, 3, :education => v[1])
data = insertcols!(data, 5, :cigsPerDay => v[2])
data = insertcols!(data,6, :BPMeds => v[3])
data = insertcols!(data, 10, :totChol => v[4])
data = insertcols!(data,13, :BMI => v[5])
data = insertcols!(data, 14, :heartRate => v[6])
data = insertcols!(data, 15, :glucose => v[7]);
first(data,5) # for showing the 1st five rows of the data

5×16 typename(DataFrame). Omitted printing of 10 columns
│ Row │ male  │ age   │ education │ currentSmoker │ cigsPerDay │ BPMeds  │
│     │ Int64 │ Int64 │ Float64   │ Int64         │ Float64    │ Float64 │
├─────┼───────┼───────┼───────────┼───────────────┼────────────┼─────────┤
│ 1   │ 1     │ 39    │ 4.0       │ 0             │ 0.0        │ 0.0     │
│ 2   │ 0     │ 46    │ 2.0       │ 0             │ 0.0        │ 0.0     │
│ 3   │ 1     │ 48    │ 1.0       │ 1             │ 20.0       │ 0.0     │
│ 4   │ 0     │ 61    │ 3.0       │ 1             │ 30.0       │ 0.0     │
│ 5   │ 0     │ 46    │ 3.0       │ 1             │ 23.0       │ 0.0     │

In [32]:
describe(data)  # description of the data

16×8 typename(DataFrame). Omitted printing of 2 columns
│ Row │ variable        │ mean       │ min   │ median  │ max   │ nunique │
│     │ Symbol          │ Float64    │ Real  │ Float64 │ Real  │ Nothing │
├─────┼─────────────────┼────────────┼───────┼─────────┼───────┼─────────┤
│ 1   │ male            │ 0.429212   │ 0     │ 0.0     │ 1     │         │
│ 2   │ age             │ 49.5849    │ 32    │ 49.0    │ 70    │         │
│ 3   │ education       │ 1.97947    │ 1.0   │ 2.0     │ 4.0   │         │
│ 4   │ currentSmoker   │ 0.494101   │ 0     │ 0.0     │ 1     │         │
│ 5   │ cigsPerDay      │ 8.94148    │ 0.0   │ 0.0     │ 70.0  │         │
│ 6   │ BPMeds          │ 0.0292591  │ 0.0   │ 0.0     │ 1.0   │         │
│ 7   │ prevalentStroke │ 0.00589901 │ 0     │ 0.0     │ 1     │         │
│ 8   │ prevalentHyp    │ 0.310524   │ 0     │ 0.0     │ 1     │         │
│ 9   │ diabetes        │ 0.0257197  │ 0     │ 0.0     │ 1     │         │
│ 10  │ totChol         │ 236.678    │ 107.0 │ 233.0   │ 696.0 │         │
│ 11  │ sysBP           │ 132.352    │ 83.5  │ 128.0   │ 295.0 │         │
│ 12  │ diaBP           │ 82.8935    │ 48.0  │ 82.0    │ 142.5 │         │
│ 13  │ BMI             │ 25.8001    │ 15.54 │ 25.38   │ 56.8  │         │
│ 14  │ heartRate       │ 75.8787    │ 44.0  │ 75.0    │ 143.0 │         │
│ 15  │ glucose         │ 81.512     │ 40.0  │ 77.0    │ 394.0 │         │
│ 16  │ TenYearCHD      │ 0.151958   │ 0     │ 0.0     │ 1     │         │

In [33]:
# what are the columns we have inside the data
names(data)

16-element Vector{Symbol}:
 :male
 :age
 :education
 :currentSmoker
 :cigsPerDay
 :BPMeds
 :prevalentStroke
 :prevalentHyp
 :diabetes
 :totChol
 :sysBP
 :diaBP
 :BMI
 :heartRate
 :glucose
 :TenYearCHD

In [34]:
eltype.(eachcol(data))
# show the datatypes for all the columns

16-element Vector{DataType}:
 Int64
 Int64
 Float64
 Int64
 Float64
 Float64
 Int64
 Int64
 Int64
 Float64
 Float64
 Float64
 Float64
 Float64
 Float64
 Int64

# Checking the unique values for each predictor

In [35]:
# counting the number for male 1st column
countmap(data[:,1])

Dict{Int64, Int64} with 2 entries:
  0 => 2419
  1 => 1819

In [42]:
# 2nd column
combine(groupby(data,:age),nrow);

In [37]:
# since this third column has 4 different values with many times repeated, so we need to combine all the rows 
combine(groupby(data,:education),nrow)

4×2 typename(DataFrame)
│ Row │ education │ x1    │
│     │ Float64   │ Int64 │
├─────┼───────────┼───────┤
│ 1   │ 4.0       │ 473   │
│ 2   │ 2.0       │ 1358  │
│ 3   │ 1.0       │ 1720  │
│ 4   │ 3.0       │ 687   │

In [38]:
# counting the number  current smoker 
countmap(data[:,4])

Dict{Int64, Int64} with 2 entries:
  0 => 2144
  1 => 2094

In [39]:
# instead of use countmap, for two different types values, we can also combine all the rows in that column
combine(groupby(data,:currentSmoker),nrow)

2×2 typename(DataFrame)
│ Row │ currentSmoker │ x1    │
│     │ Int64         │ Int64 │
├─────┼───────────────┼───────┤
│ 1   │ 0             │ 2144  │
│ 2   │ 1             │ 2094  │

In [41]:
combine(groupby(data,:cigsPerDay),nrow);

In [25]:
combine(groupby(data,:BPMeds),nrow)

2×2 DataFrame
 Row │ BPMeds   nrow  
     │ Float64  Int64 
─────┼────────────────
   1 │     0.0   4114
   2 │     1.0    124

In [26]:
combine(groupby(data,:prevalentStroke),nrow)

2×2 DataFrame
 Row │ prevalentStroke  nrow  
     │ Int64            Int64 
─────┼────────────────────────
   1 │               0   4213
   2 │               1     25

In [27]:
combine(groupby(data,:prevalentHyp),nrow)

2×2 DataFrame
 Row │ prevalentHyp  nrow  
     │ Int64         Int64 
─────┼─────────────────────
   1 │            0   2922
   2 │            1   1316

In [28]:
combine(groupby(data,:diabetes),nrow)

2×2 DataFrame
 Row │ diabetes  nrow  
     │ Int64     Int64 
─────┼─────────────────
   1 │        0   4129
   2 │        1    109

In [29]:
combine(groupby(data,:totChol),nrow);

In [30]:
length(unique(data[:,"totChol"]))

248

In [45]:
combine(groupby(data,:sysBP),nrow);
length(unique(data[:,:sysBP]))

234

In [32]:
length(unique(data[:,"diaBP"]))

146

In [33]:
combine(groupby(data,:BMI),nrow);

In [34]:
length(unique(data[:,"BMI"]))

1363

In [35]:
combine(groupby(data,:heartRate),nrow);

In [36]:
length(unique(data[:,"heartRate"]))

73

In [37]:
combine(groupby(data,:glucose),nrow);

In [38]:
length(unique(data[:,"glucose"]))

143

In [39]:
countmap(data[:,end])

Dict{Int64, Int64} with 2 entries:
  0 => 3594
  1 => 644

In [40]:
644/size(data)[1]

0.1519584709768759

In [47]:
using StatsBase

In [ ]:
B

## One hot enconding

In [59]:
Gender = select(DataFrame(gender = data[:,:male]),
    [:male => ByRow(isequal(v)) => Symbol(v) 
        for v in unique(DataFrame(gender = data[:,:male]).gender)])

LoadError: UndefVarError: ByRow not defined

In [50]:
using Distributions

Therefore, this dataset has some categorical(discrete) predictors and some numerical(continuous) predictors. The discrete predictors are  `gender`,`current smoker`,`bpmeds`,`previous stroke`,`previous hypertension`,`diabetes`.
The continuous predictors are `age`,`education`,`cigsperrate`,`totchol`,`sysbp`,`diabp`,`bmi`,`heartrate`,`glucose`.

# Data Visualization

In [41]:
# using PlotlyJS

In [42]:

features = [:male,:age,:education,:currentSmoker,:cigsPerDay,:BPMeds,:prevalentStroke,
    :prevalentHyp,:diabetes,:totChol,:sysBP,:BMI,:heartRate,:glucose]

Plot(data,dimensions = features,kind = "splom") # splom is scatter matrix plot


LoadError: UndefVarError: Plot not defined

In [43]:
# visualization of the age predictor
p = histogram(data[:,2],normalize = true,label = "age",fg_legend = false)
p1 = boxplot(data[:,2],label = :none);
plot(p,p1)


In [44]:
# visualization of education predictor
p = histogram(data[:,3],normalize = true,label = "education",fg_legend = false)
p1 = boxplot(data[:,3],label = :none);
plot(p,p1)

In [45]:
# visualization of education predictor
p = histogram(data[:,5],normalize = true,label = "cigs per day",fg_legend = false)
p1 = boxplot(data[:,5],label = :none)
plot(p,p1)

In [46]:
p = histogram(data[:,10],normalize = true,label = "total cholesterol",fg_legend = false)
p1 = boxplot(data[:,10],label = :none);
plot(p,p1)

In [47]:
p = histogram(log.(data[:,10]),normalize = true,label = "total cholesterol",fg_legend = false)
p1 = boxplot(log.(data[:,10]),label = :none);
plot(p,p1)

In [48]:
p = histogram(data[:,11],normalize = true,label = "sysbp",fg_legend = false)
p1 = boxplot(data[:,11],label = :none);
plot(p,p1)

In [49]:
p = histogram(log.(data[:,11]),normalize = true,label = "sysbp",fg_legend = false)
p1 = boxplot(log.(data[:,11]),label = :none);
plot(p,p1)

In [50]:
p = histogram(data[:,12],normalize = true,label = "diabp",fg_legend = false)
p1 = boxplot(data[:,12],label = :none);
plot(p,p1)

In [51]:
p = histogram(data[:,13],normalize = true,label = "BMI",fg_legend = false)
p1 = boxplot(data[:,13],label = :none);
plot(p,p1)

In [52]:
p = histogram(log.(data[:,13]),normalize = true,label = "bmi",fg_legend = false)
p1 = boxplot(log.(data[:,13]),label = :none);
plot(p,p1)

In [53]:
p = histogram(data[:,14],normalize = true,label = "heart rate",fg_legend = false)
p1 = boxplot(data[:,14],label = :none);
plot(p,p1)

In [54]:
p = histogram(data[:,15],normalize = true,label = "glucose",fg_legend = false)
p1 = boxplot(data[:,15],label = :none);
plot(p,p1)

In [55]:
p = histogram(log.(data[:,15]),normalize = true,label = "glucose",fg_legend = false)
p1 = boxplot(log.(data[:,15]),label = :none);
plot(p,p1)

* Normal systolic blood pressure is less than 120 mmHg.

* Normal diastolic blood pressure is less than 80.

* Normal cholesterol is 200mg/dL.

* Normal bmi rate is between 18.5 and 24.9

* Normal glucose level is 99mg/dL. 

### Treatment of the ouliers

# visualize the relation  with response and predictors

In [56]:
# plot the age predictor with response
Plots.scatter(data[:,2],data[:,16],label = :none,xlabel = "age",ylabel = "stroke")

In [57]:
# plot the cigs per day predictor with response
Plots.scatter(data[:,5],data[:,16],label = :none,xlabel = "cigs per day",ylabel = "stroke")

In [58]:
# plot the total cholesterol predictor with response
Plots.scatter(data[:,10],data[:,16],label = :none,xlabel = "totchol",ylabel = "stroke")

In [59]:
# plot the systolic blood pressure predictor with response
Plots.scatter(data[:,11],data[:,end],label = :none,xlabel = "sysbp",ylabel = "stroke")

In [60]:
# plot the diastic cholesterol predictor with response
Plots.scatter(data[:,12],data[:,16],label = :none,xlabel = "diabp",ylabel = "stroke")

In [61]:
# plot the age predictor with response
Plots.scatter(data[:,13],data[:,16],label = :none,xlabel = "bmi",ylabel = "stroke")

In [62]:
# plot the age predictor with response
Plots.scatter(data[:,14],data[:,16],label = :none,xlabel = "heartrate",ylabel = "stroke")

In [63]:
# plot the age predictor with response
Plots.scatter(data[:,15],data[:,16],label = :none,xlabel = "glucose",ylabel = "stroke")

In [64]:
df = Matrix(data);

In [65]:
cor_mat = cor(df) # this is the correlation matrix 
#print(cor_mat)

16×16 Matrix{Float64}:
  1.0         -0.0289786   0.017205    …  -0.116621    0.0111396   0.0884276
 -0.0289786    1.0        -0.163547       -0.0128477   0.117978    0.225256
  0.017205    -0.163547    1.0            -0.053683   -0.0340394  -0.0533826
  0.197596    -0.213748    0.0182727       0.0623305  -0.0554121   0.0194563
  0.31563     -0.191847    0.00761819      0.0738527  -0.0568946   0.0588591
 -0.051545     0.120955   -0.0103648   …   0.0151423   0.0491716   0.0864171
 -0.00454633   0.0576548  -0.0351496      -0.0176742   0.0188819   0.0618099
  0.00531335   0.307194   -0.0810208       0.147196    0.0837004   0.177603
  0.015708     0.101258   -0.0381362       0.0489962   0.606452    0.0973165
 -0.0693921    0.260041   -0.0223213       0.0904827   0.0458215   0.0815434
 -0.0359893    0.394302   -0.128273    …   0.182143    0.135216    0.216429
  0.0579335    0.206104   -0.0617187       0.181257    0.059118    0.145299
  0.0816604    0.135169   -0.1355          0.0675192   0.

In [66]:
## checking the imbalance of the data

countmap(data.TenYearCHD)

Dict{Int64, Int64} with 2 entries:
  0 => 3594
  1 => 644

In [67]:
(644/3594)*100
# It shows that only 17%  patient are the having true heart disease , that's a very low.

17.91875347801892

In [68]:
using Lathe.preprocess:TrainTestSplit

In [69]:
train,test =  TrainTestSplit(data,0.75); # 75% dataset is used to build the model

In [70]:
size(test),size(train)

((1092, 16), (3146, 16))

#### Building the Logistic Model

In [71]:
fm = @formula(TenYearCHD ~ male+age+education+currentSmoker+cigsPerDay+BPMeds+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+diaBP+BMI+heartRate+glucose )
log_model = glm(fm,train,Binomial(),ProbitLink())  # building the model on the training dataset

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + education + currentSmoker + cigsPerDay + BPMeds + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + diaBP + BMI + heartRate + glucose

Coefficients:
───────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
───────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.69337      0.421507     -11.13    <1e-28  -5.51951      -3.86724
male              0.20693      0.0642795      3.22    0.0013   0.0809443     0.332915
age               0.0332017    0.00399603     8.31    <1e-16   0.0253696     0.0410337
education        -0.00684702   0.0298517     -0.23    0.8186  -0.0

* By looking at the p-values for each predictor , we can say that, only male,age,cigsperday,prevalentstroke,totChol,BPMeds,sysBp,glucose are signficant predictors at 5% significance level.

In [72]:
vif(log_model)
# this computes  variance influence factor of each predictors in this logistic model.

15-element Vector{Float64}:
 1.2165523461462626
 1.3380589116161659
 1.057743487592117
 2.4541471195155977
 2.578148437396981
 1.1181979115829923
 1.029837755085312
 2.0394915019517867
 1.6209219986770933
 1.0704665534188442
 3.6150303840766904
 2.811774391751837
 1.2027689654705849
 1.1016909547401859
 1.6300734460830553

The logistic regression model returns the probability for each row. We need to convert the probabilities ti binary outcomes(0 and 1) as our problem is on binary classification(stroke or not). For that,we need to decide a cut-off. We can consider the empirical proportion of the strokes in the data as the cut-off. 

For example, in this problem, it will be the number of rows with stroke =1 divided by the number of rows in the data. 

Consider that value as cut-off and check the performence of the logistic model.

In [73]:
cut_off = 644/nrow(data)


0.1519584709768759

In [74]:
fit_predict1 = predict(log_model,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1 = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run

67.48251748251748

In [75]:
fit_predict1 = predict(log_model,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1 = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run

69.04761904761905

In [76]:
r2(log_model,:devianceratio)

0.10609081638076523

In [77]:
adjr2(log_model,:devianceratio)

0.10180690655511404

In [78]:
aic_1 = aic(log_model) ; bic_1 = bic(log_model);
aic_1,bic_1

(2362.8110839240508, 2459.6732772619425)

### Backward selection 1 remove education

In [79]:
fm = @formula(TenYearCHD ~ male+age+currentSmoker+cigsPerDay+BPMeds+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+diaBP+BMI+heartRate+glucose )
log_model_2 = glm(fm,train,Binomial(),ProbitLink()) 

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + currentSmoker + cigsPerDay + BPMeds + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + diaBP + BMI + heartRate + glucose

Coefficients:
───────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
───────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.71774      0.406837     -11.60    <1e-30  -5.51513      -3.92035
male              0.206572     0.0642711      3.21    0.0013   0.080603      0.332541
age               0.0333187    0.00396408     8.41    <1e-16   0.0255492     0.0410881
currentSmoker     0.0790558    0.0912029      0.87    0.3860  -0.0996985     0

In [80]:
fit_predict1 = predict(log_model_2,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1 = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_2,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1 = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


68.68131868131869

In [81]:
r2(log_model_2,:devianceratio)

0.10607056897849887

In [82]:
adjr2(log_model_2,:devianceratio)

0.10207343961589876

In [83]:
aic_2 = aic(log_model_2) ; bic_2 = bic(log_model_2);
aic_2,bic_2

(2360.8638777318506, 2451.672183986124)

#### 2 remove bmi

In [84]:
fm = @formula(TenYearCHD ~ male+age+currentSmoker+cigsPerDay+BPMeds+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+diaBP+heartRate+glucose )
log_model_3 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + currentSmoker + cigsPerDay + BPMeds + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + diaBP + heartRate + glucose

Coefficients:
──────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)    Lower 95%    Upper 95%
──────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.73043      0.384807     -12.29    <1e-34  -5.48464     -3.97622
male              0.206186     0.0641026      3.22    0.0013   0.0805469    0.331825
age               0.0333199    0.00396129     8.41    <1e-16   0.0255559    0.0410839
currentSmoker     0.0800689    0.0904762      0.88    0.3762  -0.0972611    0.257399
cigsP

In [85]:
fit_predict1 = predict(log_model_3,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_3,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


68.77289377289377

In [86]:
r2(log_model_3,:devianceratio)

0.10606671695259762

In [87]:
adjr2(log_model_3,:devianceratio)

0.10235626590546598

In [88]:
aic_3 = aic(log_model_3); bic_3 = bic(log_model_3);
aic_3,bic_3

(2358.873921643279, 2443.6283408139343)

## 3 remove current smoker

In [89]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+BPMeds+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+diaBP+heartRate+glucose )
log_model_4 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + BPMeds + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + diaBP + heartRate + glucose

Coefficients:
───────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
───────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.68716      0.381296     -12.29    <1e-34  -5.43449      -3.93983
male              0.204437     0.064091       3.19    0.0014   0.078821      0.330053
age               0.0330356    0.00394712     8.37    <1e-16   0.0252994     0.0407718
cigsPerDay        0.0118843    0.00256607     4.63    <1e-05   0.00685486    0.0169137
BPMeds       

In [90]:
fit_predict1 = predict(log_model_4,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_4,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


68.95604395604396

In [91]:
r2(log_model_4,:devianceratio)

0.10577257293136644

In [92]:
adjr2(log_model_4,:devianceratio)

0.10234750777821489

In [93]:
aic_4 = aic(log_model_4);bic_4 = bic(log_model_4);
aic_4,bic_4

(2357.6408833856085, 2436.3414154726456)

## 4 remove  heartrate

In [94]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+BPMeds+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+diaBP+glucose )
log_model_5 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + BPMeds + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + diaBP + glucose

Coefficients:
───────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
───────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.73659      0.349959     -13.53    <1e-41  -5.4225       -4.05068
male              0.20738      0.0633617      3.27    0.0011   0.0831937     0.331567
age               0.033142     0.00392766     8.44    <1e-16   0.0254439     0.04084
cigsPerDay        0.0117931    0.00255099     4.62    <1e-05   0.0067932     0.0167929
BPMeds            0.172009 

In [95]:
fit_predict1 = predict(log_model_5,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_5,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


68.86446886446886

In [96]:
r2(log_model_5,:devianceratio)

0.10573391397763576

In [97]:
adjr2(log_model_5,:devianceratio)

0.10259513703243917

In [98]:
aic_5 = aic(log_model_5); bic_5 = bic(log_model_5);
aic_5,bic_5

(2355.7416841375166, 2428.388329140935)

### Remove diabp

In [99]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+BPMeds+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+glucose )
log_model_6 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + BPMeds + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + glucose

Coefficients:
───────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
───────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.77465      0.315588     -15.13    <1e-50  -5.39319      -4.15611
male              0.205095     0.0627698      3.27    0.0011   0.0820687     0.328122
age               0.0333624    0.00384018     8.69    <1e-17   0.0258357     0.040889
cigsPerDay        0.011838     0.00254611     4.65    <1e-05   0.00684769    0.0168283
BPMeds            0.172099     0.1

In [100]:
fit_predict1 = predict(log_model_6,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_6,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


69.04761904761905

In [101]:
r2(log_model_6,:devianceratio)

0.10570843523547291

In [102]:
adjr2(log_model_6,:devianceratio)

0.10285583056317771

In [103]:
aic_6 = aic(log_model_6); bic_6 = bic(log_model_6);
aic_6,bic_6

(2353.8081183298555, 2420.400876249656)

# remove bpmeds

In [104]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+prevalentStroke+prevalentHyp+diabetes+
    totChol+sysBP+glucose )
log_model_7 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + prevalentStroke + prevalentHyp + diabetes + totChol + sysBP + glucose

Coefficients:
──────────────────────────────────────────────────────────────────────────────────────
                        Coef.  Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
──────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.80415      0.314358    -15.28    <1e-51  -5.42028      -4.18802
male              0.200661     0.0626679     3.20    0.0014   0.0778339     0.323488
age               0.0334212    0.00384027    8.70    <1e-17   0.0258944     0.040948
cigsPerDay        0.0118333    0.00254586    4.65    <1e-05   0.00684351    0.0168231
prevalentStroke   0.39575      0.302159      1.31 

In [105]:
fit_predict1 = predict(log_model_7,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_7,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


69.04761904761905

In [106]:
adjr2(log_model_7,:devianceratio)

0.10263563320101698

In [107]:
r2(log_model_7,:devianceratio)

0.10520360754161817

In [108]:
aic_7 = aic(log_model_7);bic_7 = bic(log_model_7);
aic_7,bic_7

(2353.1244242878543, 2413.6632951240363)

# remove diabetes

In [109]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+prevalentStroke+prevalentHyp+
    totChol+sysBP+glucose )
log_model_8 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + prevalentStroke + prevalentHyp + totChol + sysBP + glucose

Coefficients:
───────────────────────────────────────────────────────────────────────────────────────
                        Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
───────────────────────────────────────────────────────────────────────────────────────
(Intercept)      -4.8207       0.304858     -15.81    <1e-55  -5.41821      -4.22319
male              0.200907     0.0626547      3.21    0.0013   0.0781058     0.323708
age               0.0334411    0.00383843     8.71    <1e-17   0.0259179     0.0409642
cigsPerDay        0.0118295    0.00254565     4.65    <1e-05   0.00684013    0.0168189
prevalentStroke   0.394459     0.302094       1.31   

In [110]:
fit_predict1 = predict(log_model_8,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_8,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


69.04761904761905

In [111]:
r2(log_model_8,:devianceratio)

0.1051857391399883

In [112]:
adjr2(log_model_8,:devianceratio)

0.10290377736540124

In [113]:
aic_8 = aic(log_model_8);bic_8 = bic(log_model_8);
aic_8,bic_8

(2351.171015003484, 2405.655998756048)

# remove prevalent stroke

In [114]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+prevalentHyp+
    totChol+sysBP+glucose )
log_model_9 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + prevalentHyp + totChol + sysBP + glucose

Coefficients:
────────────────────────────────────────────────────────────────────────────────────
                     Coef.   Std. Error       z  Pr(>|z|)     Lower 95%    Upper 95%
────────────────────────────────────────────────────────────────────────────────────
(Intercept)   -4.82666      0.304954     -15.83    <1e-55  -5.42436      -4.22897
male           0.203169     0.062623       3.24    0.0012   0.0804302     0.325908
age            0.0336069    0.00383507     8.76    <1e-17   0.0260903     0.0411235
cigsPerDay     0.0117429    0.00254428     4.62    <1e-05   0.00675617    0.0167296
prevalentHyp   0.038896     0.0826701      0.47    0.6380  -0.123134      0.200926
totChol  

In [115]:
fit_predict1 = predict(log_model_9,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_9,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


68.86446886446886

In [116]:
r2(log_model_9,:devianceratio)

0.10456274836221569

In [117]:
adjr2(log_model_9,:devianceratio)

0.10256527839361651

In [118]:
aic_9 = aic(log_model_9);bic_9 = bic(log_model_9);
aic_9,bic_9

(2350.795423653293, 2399.2265203222387)

# remove totchol

In [119]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+prevalentHyp+
    sysBP+glucose )
log_model_10 = glm(fm,train,Binomial(),ProbitLink())

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + prevalentHyp + sysBP + glucose

Coefficients:
─────────────────────────────────────────────────────────────────────────────────
                    Coef.  Std. Error       z  Pr(>|z|)    Lower 95%    Upper 95%
─────────────────────────────────────────────────────────────────────────────────
(Intercept)   -4.68874     0.280091    -16.74    <1e-62  -5.23771     -4.13978
male           0.195866    0.0622367     3.15    0.0016   0.0738843    0.317848
age            0.0341631   0.00379964    8.99    <1e-18   0.0267159    0.0416102
cigsPerDay     0.0118682   0.0025408     4.67    <1e-05   0.00688832   0.0168481
prevalentHyp   0.0401322   0.0827053     0.49    0.6275  -0.121967     0.202232
sysBP          0.00909699  0.00176527    5.

In [120]:
fit_predict1 = predict(log_model_10,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat1[2,2] + conf_mat1[1,1])/sum(conf_mat1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_10,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat1 = [v1.tn v1.fp; v1.fn v1.tp]
acc1_test = ((conf_mat1[2,2]+conf_mat1[1,1])/sum(conf_mat1))*100 # this is test accuracy in one times run


69.04761904761905

In [121]:
r2(log_model_10,:devianceratio)

0.10402455943635636

In [122]:
adjr2(log_model_10,:devianceratio)

0.1023119590402487

In [123]:
aic_10 = aic(log_model_10);bic_10 = bic(log_model_10);
aic_10,bic_10

(2350.1987168922874, 2392.5759264776148)

# remove prevalenthyp

* Only taking the significant predictors and run one times the model.

In [124]:
fm = @formula(TenYearCHD ~ male+age+cigsPerDay+
    sysBP+glucose )
log_model_1 = glm(fm,train,Binomial(),ProbitLink())  # building the model on the training dataset
fit_predict1 = predict(log_model_1,select(train,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,train[:,end])
conf_mat_train_1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_train = ((conf_mat_train_1[2,2] + conf_mat_train_1[1,1])/sum(conf_mat_train_1))*100 # train accuracy in one times run
fit_predict1 = predict(log_model_1,select(test,Not([16])))
fit_predict1 = Vector{Int64}(fit_predict1 .> cut_off)
v1 = roc(fit_predict1,test[:,end])
conf_mat_test_1 = [v1.tn v1.fp; v1.fn v1.tp]
acc_test = ((conf_mat_test_1[2,2]+conf_mat_test_1[1,1])/sum(conf_mat_test_1))*100; # this is test accuracy in one times run

In [125]:
log_model_1

StatsModels.TableRegressionModel{GeneralizedLinearModel{GLM.GlmResp{Vector{Float64}, Binomial{Float64}, ProbitLink}, GLM.DensePredChol{Float64, LinearAlgebra.CholeskyPivoted{Float64, Matrix{Float64}}}}, Matrix{Float64}}

TenYearCHD ~ 1 + male + age + cigsPerDay + sysBP + glucose

Coefficients:
────────────────────────────────────────────────────────────────────────────────
                   Coef.  Std. Error       z  Pr(>|z|)    Lower 95%    Upper 95%
────────────────────────────────────────────────────────────────────────────────
(Intercept)  -4.75526     0.243728    -19.51    <1e-84  -5.23296     -4.27756
male          0.19694     0.0621819     3.17    0.0015   0.0750657    0.318814
age           0.0342411   0.00379484    9.02    <1e-18   0.0268034    0.0416789
cigsPerDay    0.0118644   0.00254071    4.67    <1e-05   0.00688467   0.0168441
sysBP         0.00966373  0.00131867    7.33    <1e-12   0.00707919   0.0122483
glucose       0.00523161  0.00119934    4.36    <1e-04   0.002880

In [126]:
adjr2(log_model_1,:devianceratio)

0.1025065948125582

In [127]:
r2(log_model_1,:devianceratio)

0.10393345237247475

In [128]:
AIC = aic(log_model_1);BIC = bic(log_model_1);
AIC,BIC

(2348.4362727404655, 2384.759595242175)

In [129]:
conf_mat_train_1

2×2 Matrix{Int64}:
 1825  160
  864  297

In [130]:
conf_mat_test_1

2×2 Matrix{Int64}:
 621   57
 284  130

In [131]:
acc_train

67.45073108709472

In [132]:
acc_test

68.77289377289377

In [133]:
rep = 500
train_conf_mat = []
test_conf_mat = []
for i in 1:rep
    train_data,test_data = TrainTestSplit(data,0.6)
    fm = @formula(TenYearCHD ~ male+age+cigsPerDay
        +sysBP+glucose)
    log_model = glm(fm,train_data,Binomial(),ProbitLink())
    fit_predict = predict(log_model,select(train_data,Not([16])))
    fit_predict = Vector{Int64}(fit_predict .> cut_off)
    v = MLBase.roc(fit_predict,train_data[:,end])
    conf_matrix = [v.tn v.fp; v.fn v.tp]
    push!(train_conf_mat,conf_matrix)
    
    fit_predict_test = predict(log_model,select(test_data,Not([16])))
    fit_predict_test = Vector{Int64}(fit_predict_test .> cut_off)
    v = MLBase.roc(fit_predict_test,test_data[:,end])
    conf_matrix = [v.tn v.fp; v.fn v.tp]
    push!(test_conf_mat,conf_matrix)
end

train_acc_overall = []
test_acc_overall = []
train_acc_correct = []
test_acc_correct  = []
for i in 1:rep
    mat = train_conf_mat[i]
    push!(train_acc_correct,mat[2,2]/(mat[2,1] + mat[2,2]))
    push!(train_acc_overall,(mat[1,1] + mat[2,2])/sum(mat))
end

for i in 1:rep
    mat = test_conf_mat[i]
    push!(test_acc_correct,mat[2,2]/(mat[2,1] + mat[2,2]))
    push!(test_acc_overall,(mat[1,1] + mat[2,2])/sum(mat))
end

In [134]:
mean(train_acc_overall) # after run the model 500 times, training accuracy is 66.8%

0.6663181555584443

In [135]:
mean(test_acc_overall) # after run the model 500 times, testing accuracy is 66.6%

0.6643656874595357

In [136]:
boxplot(train_acc_overall,label = "train")
boxplot!(test_acc_overall,label = "test",
    title = "Overall accuracy",legend = :topleft)

In [137]:
boxplot(train_acc_correct,label = "train")
boxplot!(test_acc_correct,label = "test",
    title = "True positive rate",legend = :topleft)

In [138]:
density(train_acc_correct,label = "train") 
density!(test_acc_correct,label = "test",title = "Probability of Correct")

In [139]:
density(train_acc_overall,label = "train") 
density!(test_acc_overall,label = "test",title = "Overall Accuracy")

So, in Logistic regression model gives us 66.4% accuracy on training data set and on testing dataset gives 66.2% accuracy.

# Use Decision Tree model

In [140]:
using DecisionTree

In [141]:
train,test = TrainTestSplit(data,0.7)
train_pred = train[:,1:end-1]
train_response = train[:,end];

In [142]:
size(train),size(test)

((2963, 16), (1275, 16))

In [143]:
test_pred = test[:,1:end-1]
test_response = test[:,end];

In [144]:
training_pred = Matrix(train_pred);

In [145]:
model = DecisionTreeClassifier(max_depth = 7)
DecisionTree.fit!(model,training_pred,train_response)

DecisionTreeClassifier
max_depth:                7
min_samples_leaf:         1
min_samples_split:        2
min_purity_increase:      0.0
pruning_purity_threshold: 1.0
n_subfeatures:            0
classes:                  [0, 1]
root:                     Decision Tree
Leaves: 71
Depth:  7

In [295]:
plot(model)

LoadError: Cannot convert RandomForestClassifier to series data for plotting

In [146]:
print_tree(model)

Feature 2 < 48.5 ?
├─ Feature 5 < 16.5 ?
    ├─ Feature 12 < 109.2 ?
        ├─ Feature 2 < 39.5 ?
            ├─ Feature 11 < 116.2 ?
                ├─ Feature 3 < 3.5 ?
                    ├─ Feature 10 < 307.0 ?
                        ├─ 0 : 110/112
                        └─ 1 : 1/1
                    └─ Feature 10 < 230.5 ?
                        ├─ 0 : 12/13
                        └─ 1 : 3/3
                └─ 0 : 134/134
            └─ Feature 11 < 118.8 ?
                ├─ Feature 15 < 75.5 ?
                    ├─ Feature 10 < 239.5 ?
                        ├─ 0 : 56/64
                        └─ 0 : 27/27
                    └─ 0 : 155/155
                └─ Feature 14 < 78.5 ?
                    ├─ Feature 14 < 69.5 ?
                        ├─ 0 : 91/96
                        └─ 0 : 122/144
                    └─ Feature 15 < 80.5 ?
                        ├─ 0 : 83/90
                        └─ 0 : 69/69
        └─ Feature 14 < 67.5 ?
            ├─ 1 : 2/2
      

In [147]:
prediction_train = DecisionTree.predict(model,Matrix(train_pred))
acc_train = mean(prediction_train .== train_response)

0.8747890651366858

In [148]:
prediction_test = DecisionTree.predict(model,Matrix(test_pred));
acc_test = mean(prediction_test .== test_response) 
# accuracy of the  decision tree model

0.8462745098039216

In [149]:
train_conf_mat = DecisionTree.confusion_matrix(train_response,
    prediction_train)

2×2 Matrix{Int64}:
 2485   21
  350  107

Classes:  [0, 1]
Matrix:   
Accuracy: 0.8747890651366858
Kappa:    0.31990957476754905

In [150]:
countmap(train_response)

Dict{Int64, Int64} with 2 entries:
  0 => 2506
  1 => 457

In [151]:
test_conf_mat = DecisionTree.confusion_matrix(test_response,
    prediction_test)

2×2 Matrix{Int64}:
 1052  36
  160  27

Classes:  [0, 1]
Matrix:   
Accuracy: 0.8462745098039216
Kappa:    0.15342087076710467

In [152]:
prob = DecisionTree.predict_proba(model,Matrix(test_pred)) 
# it gives the probability for each rows in our testing data set

1275×2 Matrix{Float64}:
 0.923077  0.0769231
 0.922222  0.0777778
 0.798913  0.201087
 0.844358  0.155642
 0.831461  0.168539
 1.0       0.0
 0.703704  0.296296
 0.564516  0.435484
 1.0       0.0
 1.0       0.0
 1.0       0.0
 0.798913  0.201087
 0.0       1.0
 ⋮         
 0.922222  0.0777778
 0.911111  0.0888889
 1.0       0.0
 1.0       0.0
 0.847222  0.152778
 1.0       0.0
 0.798913  0.201087
 0.844358  0.155642
 0.703704  0.296296
 0.844358  0.155642
 0.847222  0.152778
 0.962687  0.0373134

# run the model decision tree 100 times with all predictors

In [228]:
rep = 100
conf_mat_train = []
conf_mat_test = []
train_acc_overall = []
test_acc_overall = []
for i in 1:rep
    train,test = TrainTestSplit(data,0.7)
    train_pred = train[:,1:end-1]
    train_response = train[:,end];
    test_pred = test[:,1:end-1]
    test_response = test[:,end];
    training_pred = Matrix(train_pred);
    model = DecisionTreeClassifier(max_depth = 7)
    DecisionTree.fit!(model,training_pred,train_response)
    prediction_train = DecisionTree.predict(model,Matrix(train_pred))
    push!(conf_mat_train,DecisionTree.confusion_matrix(train_response,prediction_train))
    push!(train_acc_overall,mean(prediction_train .== train_response))
    
    
    prediction_test = DecisionTree.predict(model,Matrix(test_pred));
    push!(conf_mat_test,DecisionTree.confusion_matrix(test_response,prediction_test))
    push!(test_acc_overall,mean(prediction_test .== test_response))
end
    
    
    

In [229]:
mean(train_acc_overall),mean(test_acc_overall)

(0.8760573533104998, 0.8340780009856804)

In [154]:

p = boxplot(train_acc_overall,label = "train accuracy")
p1 = boxplot(test_acc_overall,label = "test accuracy");

plot(p,p1)

In [155]:
density(train_acc_overall,label = "train")
density!(test_acc_overall,label ="test" )

#### Random Forest Classifier

In [156]:
model_1 = RandomForestClassifier(n_trees = 500)
DecisionTree.fit!(model_1,training_pred,train_response)

RandomForestClassifier
n_trees:             500
n_subfeatures:       -1
partial_sampling:    0.7
max_depth:           -1
min_samples_leaf:    1
min_samples_split:   2
min_purity_increase: 0.0
classes:             [0, 1]
ensemble:            Ensemble of Decision Trees
Trees:      500
Avg Leaves: 294.382
Avg Depth:  22.476

In [157]:
prediction_train = DecisionTree.predict(model_1,Matrix(train_pred))
acc_train = mean(prediction_train .== train_response)

0.9976494291470785

In [158]:
train_conf_mat = DecisionTree.confusion_matrix(train_response,prediction_train)

2×2 Matrix{Int64}:
 2530    0
    7  441

Classes:  [0, 1]
Matrix:   
Accuracy: 0.9976494291470785
Kappa:    0.9907445968709402

In [159]:
prediction_test = DecisionTree.predict(model_1,Matrix(test_pred));
acc_test = mean(prediction_test .== test_response) # accuracy of the  decision tree model

0.8420634920634921

In [160]:
test_conf_mat = DecisionTree.confusion_matrix(test_response,prediction_test)

2×2 Matrix{Int64}:
 1055  9
  190  6

Classes:  [0, 1]
Matrix:   
Accuracy: 0.8420634920634921
Kappa:    0.03554119547657522

In [161]:
sum(train_response .== 0)

2530

### Oversampling

In [162]:
rep = 100
train_conf_mat = []
test_conf_mat = []
for i in 1:rep
    major_ind = findall(x -> x ==0,data[:,end])
    minor_ind = findall(x -> x == 1,data[:,end])
    minor_ind = sample(minor_ind,length(major_ind));
     
end

In [163]:
major_ind = findall(x -> x ==0,data[:,end])
minor_ind = findall(x -> x == 1,data[:,end]);
# minor_ind = sample(minor_ind,length(major_ind))
#data[:,end] = [zeros(length(minor_ind));ones(length(major_ind))]
length(major_ind),length(minor_ind)

(3594, 644)

In [258]:
minor = sample(minor_ind,length(major_ind));

In [261]:
new_data =vcat(data[minor,1:end],data[major_ind,1:end]);

In [296]:
rep = 500
train_conf_mat = []
test_conf_mat = []
for i in 1:rep
    major_ind = findall(x -> x ==0,data[:,end])
    minor_ind = findall(x -> x == 1,data[:,end])
    minor_ind = sample(minor_ind,length(major_ind))
    new_data =vcat(data[minor,1:end],data[major_ind,1:end])
    train_data,test_data = TrainTestSplit(new_data,0.7)
    fm = @formula(TenYearCHD ~ male+age+cigsPerDay
        +sysBP+glucose)
    log_model = glm(fm,train_data,Binomial(),ProbitLink())
    fit_predict = predict(log_model,select(train_data,Not([16])))
    fit_predict = Vector{Int64}(fit_predict .> cut_off)
    v = MLBase.roc(fit_predict,train_data[:,end])
    conf_matrix = [v.tn v.fp; v.fn v.tp]
    push!(train_conf_mat,conf_matrix)
    
    fit_predict_test = predict(log_model,select(test_data,Not([16])))
    fit_predict_test = Vector{Int64}(fit_predict_test .> cut_off)
    v = MLBase.roc(fit_predict_test,test_data[:,end])
    conf_matrix = [v.tn v.fp; v.fn v.tp]
    push!(test_conf_mat,conf_matrix)
end

train_acc_overall = []
test_acc_overall = []
train_acc_correct = []
test_acc_correct  = []
for i in 1:rep
    mat = train_conf_mat[i]
    push!(train_acc_correct,mat[2,2]/(mat[2,1] + mat[2,2]))
    push!(train_acc_overall,(mat[1,1] + mat[2,2])/sum(mat))
end

for i in 1:rep
    mat = test_conf_mat[i]
    push!(test_acc_correct,mat[2,2]/(mat[2,1] + mat[2,2]))
    push!(test_acc_overall,(mat[1,1] + mat[2,2])/sum(mat))
end

In [297]:
mean(train_acc_overall)

0.5201962255591298

In [298]:
mean(test_acc_overall)

0.5204312043456796

In [299]:
major_ind = findall(x -> x ==0,data[:,end])
minor_ind = findall(x -> x == 1,data[:,end])
minor_ind = sample(minor_ind,length(major_ind))

new_data =vcat(data[minor,1:end],data[major_ind,1:end])
train,test = TrainTestSplit(new_data,0.7)
train_pred = train[:,1:end-1]
train_response = train[:,end];
test_pred = test[:,1:end-1]
test_response = test[:,end];
training_pred = Matrix(train_pred);
model = DecisionTreeClassifier(max_depth = 7)
DecisionTree.fit!(model,training_pred,train_response)
prediction_train = DecisionTree.predict(model,Matrix(train_pred))
train_conf = DecisionTree.confusion_matrix(train_response,prediction_train) #training confusion matrix
mean(prediction_train.== train_response)


0.7450941526263627

In [266]:
sum(prediction_train .!== train_response)

1230

In [267]:
countmap(train[:,end])

Dict{Int64, Int64} with 2 entries:
  0 => 2504
  1 => 2474

In [268]:
train_conf

2×2 Matrix{Int64}:
 1807   697
  533  1941

Classes:  [0, 1]
Matrix:   
Accuracy: 0.7529128163921254
Kappa:    0.5060038506743845

In [300]:
prediction_test = DecisionTree.predict(model,Matrix(test_pred))
test_conf = DecisionTree.confusion_matrix(test_response,prediction_test)
mean(prediction_test.==test_response)

0.700886607559496

In [270]:
test_conf

2×2 Matrix{Int64}:
 738  352
 300  820

Classes:  [0, 1]
Matrix:   
Accuracy: 0.7049773755656109
Kappa:    0.40946869723447166

In [271]:
countmap(test[:,end])

Dict{Int64, Int64} with 2 entries:
  0 => 1090
  1 => 1120

In [272]:
rep = 100
conf_mat_train = []
conf_mat_test = []
train_acc_overall = []
test_acc_overall = []
for i in 1:rep
    
    train,test = TrainTestSplit(new_data,0.7)
    train_pred = train[:,1:end-1]
    train_response = train[:,end];
    test_pred = test[:,1:end-1]
    test_response = test[:,end];
    training_pred = Matrix(train_pred);
    model = DecisionTreeClassifier(max_depth = 7)
    DecisionTree.fit!(model,training_pred,train_response)
    prediction_train = DecisionTree.predict(model,Matrix(train_pred))
    push!(conf_mat_train,DecisionTree.confusion_matrix(train_response,prediction_train))
    push!(train_acc_overall,mean(prediction_train .== train_response))
    
    
    prediction_test = DecisionTree.predict(model,Matrix(test_pred));
    push!(conf_mat_test,DecisionTree.confusion_matrix(test_response,prediction_test))
    push!(test_acc_overall,mean(prediction_test .== test_response))
end

In [273]:
mean(train_acc_overall)

0.741082781490193

In [274]:
mean(test_acc_overall)

0.7040534118912848

In [275]:
conf_mat_train[1]

2×2 Matrix{Int64}:
 1794   762
  526  1944

Classes:  [0, 1]
Matrix:   
Accuracy: 0.7437325905292479
Kappa:    0.48813783828747137

In [276]:
countmap(train[:,end])

Dict{Int64, Int64} with 2 entries:
  0 => 2478
  1 => 2487

In [238]:
conf_mat_test[50]

2×2 Matrix{Int64}:
 655  427
 197  819

Classes:  [0, 1]
Matrix:   
Accuracy: 0.7025738798856054
Kappa:    0.40864141540985566

In [241]:
countmap(test[:,end])

Dict{Int64, Int64} with 2 entries:
  0 => 1041
  1 => 1071

In [256]:
new_data

7188×16 DataFrame
  Row │ male   age    education  currentSmoker  cigsPerDay  BPMeds   prevalent ⋯
      │ Int64  Int64  Float64    Int64          Float64     Float64  Int64     ⋯
──────┼─────────────────────────────────────────────────────────────────────────
    1 │     0     38        2.0              1        10.0      0.0            ⋯
    2 │     1     61        2.0              0         0.0      0.0
    3 │     0     59        2.0              0         0.0      1.0
    4 │     1     41        2.0              1        20.0      0.0
    5 │     0     45        1.0              0         0.0      0.0            ⋯
    6 │     0     38        2.0              1        10.0      0.0
    7 │     1     52        1.0              1        25.0      0.0
    8 │     0     44        1.0              0         0.0      0.0
    9 │     1     52        1.0              0         0.0      0.0            ⋯
   10 │     0     53        4.0              0         0.0      0.0
   11 │     0     42        2.0              0         0.0      0.0
  ⋮   │   ⋮      ⋮        ⋮            ⋮            ⋮          ⋮            ⋮  ⋱
 7179 │     1     45        4.0              1        43.0      0.0
 7180 │     1     43        4.0              1        20.0      0.0            ⋯
 7181 │     0     50        1.0              0         0.0      0.0
 7182 │     0     51        3.0              1        20.0      0.0
 7183 │     0     56        1.0              1         3.0      0.0
 7184 │     1     58        3.0              0         0.0      0.0            ⋯
 7185 │     1     51        3.0              1        43.0      0.0
 7186 │     0     48        2.0              1        20.0      0.0
 7187 │     0     44        1.0              1        15.0      0.0
 7188 │     0     52        2.0              0         0.0      0.0            ⋯
                                                10 columns and 7167 rows omitted

In [281]:
train,test = TrainTestSplit(new_data,0.7)
train_pred = train[:,1:end-1]
train_response = train[:,end];
test_pred = test[:,1:end-1]
test_response = test[:,end];
training_pred = Matrix(train_pred);
model = RandomForestClassifier(n_trees = 500)
DecisionTree.fit!(model,training_pred,train_response)
prediction_train = DecisionTree.predict(model,Matrix(train_pred))
train_conf = DecisionTree.confusion_matrix(train_response,prediction_train) #training confusion matrix
mean(prediction_train.== train_response)

1.0

In [282]:
train_conf

2×2 Matrix{Int64}:
 2500     0
    0  2553

Classes:  [0, 1]
Matrix:   
Accuracy: 1.0
Kappa:    1.0

In [283]:
prediction_test = DecisionTree.predict(model,Matrix(test_pred))
test_conf = DecisionTree.confusion_matrix(test_response,prediction_test)
mean(prediction_test.==test_response)

0.94192037470726

In [284]:
test_conf

2×2 Matrix{Int64}:
 981   113
  11  1030

Classes:  [0, 1]
Matrix:   
Accuracy: 0.94192037470726
Kappa:    0.8840443359376712

In [288]:
rep = 100
conf_mat_train = []
conf_mat_test = []
train_acc_overall = []
test_acc_overall = []
for i in 1:rep
    train,test = TrainTestSplit(new_data,0.7)
    train_pred = train[:,1:end-1]
    train_response = train[:,end];
    test_pred = test[:,1:end-1]
    test_response = test[:,end];
    training_pred = Matrix(train_pred);
    model = RandomForestClassifier(n_trees = 500)
    DecisionTree.fit!(model,training_pred,train_response)
    prediction_train = DecisionTree.predict(model,Matrix(train_pred))
    push!(conf_mat_train,DecisionTree.confusion_matrix(train_response,prediction_train))
    push!(train_acc_overall,mean(prediction_train .== train_response))
    
    
    prediction_test = DecisionTree.predict(model,Matrix(test_pred));
    push!(conf_mat_test,DecisionTree.confusion_matrix(test_response,prediction_test))
    push!(test_acc_overall,mean(prediction_test .== test_response))
end

In [289]:
mean(train_acc_overall)

0.9999325066857796

In [290]:
mean(test_acc_overall)

0.9457376304662038

In [293]:
conf_mat_train[30]

2×2 Matrix{Int64}:
 2508     0
    0  2557

Classes:  [0, 1]
Matrix:   
Accuracy: 1.0
Kappa:    1.0

In [294]:
conf_mat_test[30]

2×2 Matrix{Int64}:
 984   102
   7  1030

Classes:  [0, 1]
Matrix:   
Accuracy: 0.9486575600565238
Kappa:    0.8974722853462908

In [301]:
using StatsBase

In [302]:
indicatormat(["a", "b", "c", "a", "b", "d"])

4×6 Matrix{Bool}:
 1  0  0  1  0  0
 0  1  0  0  1  0
 0  0  1  0  0  0
 0  0  0  0  0  1